In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

비보호좌회전, 신호우회전, 유턴

줄임말 목록
- `i` : 교차로번호, `inter_no`
- `f` : 진입, from, `inc_edge_id`
- `t` : 진출, to, `out_edge_id`
- `vec` : 방향벡터, unit vector (`np.array([0.6, 0.8])`)
- `dire` : 방위, direction (동, 서, 남, 북, 북동, 북서, 남동, 남서)
- `rvec` : 정방향 방향벡터, unit vector to the right direction (`np.array([0,1])`)

필요한 객체들 목록

- `inter2dire2rvec` : `inter_no` $\mapsto$ `dire2rvec`
  - `dire2rvec` : `dire` $\mapsto$ `rvec`
- `inter2incs` : `inter_no` $\mapsto$ `inc_edge_ids`
- `inter2outs` : `inter_no` $\mapsto$ `out_edge_ids`
- `inter2inc2dire` : `inter_no` $\mapsto$ `int2dire`
  - `inc2dire` : `out_edge_id` $\mapsto$ `dire`
- `inter2out2dire` : `inter_no` $\mapsto$ `out2dire`
  - `out2dire` : `inc_edge_id` $\mapsto$ `dire`
- `inter2inc2vec` : `inter_no` $\mapsto$ `int2vec`
  - `inc2vec` : `out_edge_id` $\mapsto$ `vec`
- `inter2out2vec` : `inter_no` $\mapsto$ `out2vec`
  - `out2vec` : `inc_edge_id` $\mapsto$ `vec`

좌회전 판단

Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.

In [2]:
self = DailyPreprocessor()
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2. 중간산출물을 생성합니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [8]:
display(self.match4.head())
display(self.match5.head())
display(self.match6.head())
print((self.match5.head()==self.match6.head()).all().all())

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle out_angle
0       175         1         A        8        남        북       179       000
1       175         1         B        4        북        남       001       180
2       175         2         A        7        북        동       001       090
3       175         2         B        3        남        서       179       270
4       175         3         A        6        동        서       090       270

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id  
0       000  -571542797_02  571500487_01      i0  
1       180  -571500487_01  571542797_02      i0  
2       090  -571500487_01  571545870_01      i0  
3       270  -571542797_02  571510153_01      i0  
4       270   571545870_02  571510153_01      i0

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id  
0       000  -571542797_02  571500487_01      i0  
1       180  -571500487_01  571542797_02      i0  
2       090  -571500487_01  571545870_01      i0  
3       270  -571542797_02  571510153_01      i0  
4       270   571545870_02  571510153_01      i0

True


In [4]:
self.load_data()
self.get_matches()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2-1. 매칭 테이블들을 생성했습니다.


In [5]:
self.match6[40:100]

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
40       178         2         A       20      NaN      NaN       NaN   
41       178         2         B       20      NaN      NaN       NaN   
42       178         3         A       20      NaN      NaN       NaN   
43       178         3         B       20      NaN      NaN       NaN   
44       178         4         A       20      NaN      NaN       NaN   
45       178         4         B       20      NaN      NaN       NaN   
46       178         1         A        8        남        북       180   
47       178         1         B        4        북        남       000   
48       178         2         A        7        북        동       000   
49       178         2         B        3        남        서       180   
50       178         3         A        5        서        북       270   
51       178         3         B        2        서        동       270   
52       178         4         A        6        동        서       090   
53       178         4         B        1        동        남       090   
54       178         1         A        8        남        북       180   
55       178         1         B        4        북        남       000   
56       178         2         A        7        북        동       000   
57       178         2         B        3        남        서       180   
58       178         3         A        5        서        북       270   
59       178         3         B        2        서        동       270   
60       178         4         A        6        동        서       090   
61       178         4         B        1        동        남       090   
62       178         1         A        8        남        북       180   
63       178         1         B        4        북        남       000   
64       178         2         A        7        북        동       000   
65       178         2         B        3        남        서       180   
66       178         3         A        5        서        북       270   
67       178         3         B        2        서        동       270   
68       178         4         A        6        동        서       090   
69       178         4         B        1        동        남       090   
70       178         1         A        8        남        북       180   
71       178         1         B        4        북        남       000   
72       178         2         A        7        북        동       000   
73       178         2         B        3        남        서       180   
74       178         3         A        5        서        북       270   
75       178         3         B        2        서        동       270   
76       178         4         A        6        동        서       090   
77       178         4         B        1        동        남       090   
78       201         1         A        8        남        북       180   
79       201         1         B        3        남        서       180   
80       201         2         A        5        서        북       270   
81       201         2         B        2        서        동       270   
82       201         3         A        6        동        서       090   
83       201         3         B        2        서        동       270   
84       201         4         A        6        동        서       090   
85       201         4         B        1        동        남       090   
86       201         5         A        7        북        동       000   
87       201         5         B        4        북        남       000   
88       202         1         A        6        동        서       090   
89       202         1         B        2        서        동       270   
90       202         2         A       17      NaN      NaN       NaN   
91       202         2         B       18      NaN      NaN       NaN   
92       206         1         A        8        남        북       180   
93       206         1         B        4        북        남   

In [6]:
self.matching

inter_no  move_no inc_dire out_dire       inc_edge_id    out_edge_id  \
0        175        1        동        남      571545870_02   571542797_02   
1        175        2        서        동      571510153_02   571545870_01   
2        175        3        남        서     -571542797_02   571510153_01   
3        175        4        북        남     -571500487_01   571542797_02   
4        175        5        서        북      571510153_02   571500487_01   
..       ...      ...      ...      ...               ...            ...   
71       210       21        북        서  571511538_02.121   571500535_01   
72       210       21        서        남   571500535_02.18   571500585_01   
73       210       21        남        동      571500585_02   571542115_01   
74       210       21        동        북     -571542115_01   571511538_01   
75       210        5        서        북      571500535_02  -571500535_02   

   node_id  
0       i0  
1       i0  
2       i0  
3       i0  
4       i0  
..     ...  
71      i6  
72      i6  
73      i6  
74      i6  
75     u60  

[76 rows x 7 columns]